In [18]:
from datasets import load_dataset

In [19]:
ds = load_dataset("csv", data_files="https://zenodo.org/record/3257041/files/xml2csv_alto.csv?download=1")

Using custom data configuration default-0663d2a6043864fc
Reusing dataset csv (/Users/dvanstrien/.cache/huggingface/datasets/csv/default-0663d2a6043864fc/0.0.0/51cce309a08df9c4d82ffd9363bbe090bf173197fc01a71b034e8594995a1a58)
100%|██████████| 1/1 [00:00<00:00,  1.20it/s]


In [5]:
def parse_wc(example):
    if wc := example['wc']:
        wc = wc.split(" ")
        wc = [float(x) for x in wc]
        return wc
    else:
        return []

In [6]:
ds = ds.map(lambda x: {"wc":parse_wc(x)},num_proc=4, writer_batch_size=3000)

Parameter 'function'=<function <lambda> at 0x124f309d0> of the transform datasets.arrow_dataset.Dataset._map_single couldn't be hashed properly, a random hash was used instead. Make sure your transforms and parameters are serializable with pickle or dill for the dataset fingerprinting and caching to work. If you reuse this transform, the caching mechanism will consider it to be different from the previous calls and recompute everything. This warning is only showed once. Subsequent hashing failures won't be showed.


In [ ]:
!wget -O corpus-language.pkl https://zenodo.org/record/3257041/files/corpus-language.pkl?download=1

In [3]:
import pickle

In [9]:
with open("corpus-language.pkl","rb") as f:
    data = pickle.load(f)

In [10]:
data

ppn      filename language  confidence
0     PPN646426230  00000045.xml       fr         1.0
1     PPN646426230  00000218.xml       fr         1.0
2     PPN646426230  00000394.xml       fr         1.0
3     PPN646426230  00000071.xml       fr         1.0
4     PPN646426230  00000317.xml       fr         1.0
...            ...           ...      ...         ...
7479  PPN821899872  00000017.xml       de         1.0
7480  PPN821899872  00000510.xml       de         1.0
7481  PPN821899872  00000487.xml       de         1.0
7482  PPN821899872  00000187.xml       de         1.0
7483  PPN821899872  00000274.xml       de         1.0

[4734627 rows x 4 columns]

In [11]:
data['in'] = data['ppn'] + "_" + data['filename']

In [12]:
data = data.drop_duplicates(subset=['in'])

In [13]:
data = data.set_index("in")

In [14]:
data

ppn      filename language  confidence
in                                                                        
PPN646426230_00000045.xml  PPN646426230  00000045.xml       fr         1.0
PPN646426230_00000218.xml  PPN646426230  00000218.xml       fr         1.0
PPN646426230_00000394.xml  PPN646426230  00000394.xml       fr         1.0
PPN646426230_00000071.xml  PPN646426230  00000071.xml       fr         1.0
PPN646426230_00000317.xml  PPN646426230  00000317.xml       fr         1.0
...                                 ...           ...      ...         ...
PPN821899872_00000017.xml  PPN821899872  00000017.xml       de         1.0
PPN821899872_00000510.xml  PPN821899872  00000510.xml       de         1.0
PPN821899872_00000487.xml  PPN821899872  00000487.xml       de         1.0
PPN821899872_00000187.xml  PPN821899872  00000187.xml       de         1.0
PPN821899872_00000274.xml  PPN821899872  00000274.xml       de         1.0

[4697574 rows x 4 columns]

In [16]:
lookup_dict = data.to_dict('index')

In [21]:
def lookup_lang_confidence(example):
    ppn = example['ppn']
    fname = example['file name']
    if match := lookup_dict.get(f"PPN{ppn}_{fname}"):
        return {"language": match['language'],'language_confidence': match['confidence']}
    else:
        return {"language": None,"language_confidence": None}

In [23]:
lookup_lang_confidence(ds['train'][1])

{'language': 'fr', 'language_confidence': 1.0}

In [ ]:
ds = ds.map(lambda x:lookup_lang_confidence(x))

  0%|          | 0/4988099 [00:00<?, ?ex/s]

In [ ]:
ds.push_to_hub('biglam/berlin_state_library_ocr')